In [1]:
import selenium
from selenium import webdriver
from selenium.webdriver.common.keys import Keys
import os
import pandas as pd
import argparse
import string
import pandas as pd
import json
from utils.utils import get_logs
import time
from tqdm import tqdm

In [2]:
MANGO_URL = 'https://www.mangoplate.com/'
KAKAO_URL = 'https://map.kakao.com/'
GOOGLE_URL = 'https://www.google.com/maps'
# OK - 기존과 바뀜 - 함수 통일화
ALPHABET = list(string.ascii_uppercase)

logger_1, logger_2 = get_logs()
parser = argparse.ArgumentParser(description='parse')
# argument는 원하는 만큼 추가한다.
parser.add_argument('--output_dir', type=str, default = './output/seoul/mango')
parser.add_argument('--data_dir', type=str, default = './data/seoul/강서구.json')
parser.add_argument('--where', type=str, choices=['mango','google','kakao'], default='mango')
parser.add_argument('--wait_second', type=int, default = 2)
args, _ = parser.parse_known_args()
if args.where == 'mango':
    default_url = MANGO_URL
    
elif args.where == 'kakao':
    default_url = KAKAO_URL
    
elif args.where == 'google':
    default_url = GOOGLE_URL

In [3]:
# page 내에서 information 가져오기
def get_information_from_page(value, page=1):
    # 음식점이 존재하는 경우
    try:
        score = driver.find_element(value=f"body > main > article > div.column-wrapper > div > div > section > div.search-list-restaurants-inner-wrap > ul > li.list-restaurant.server_render_search_result_item > div.list-restaurant-item > figure > figcaption > div",  by = 'css selector')
    except:
        # 유일하지 않은 경우
        value['mango_score'].append(None)
        # 아예 존재하지 않는 경우
        return page
    # 한 페이지 내
    for i in range(1,12):
        for j in range(1,3):
            try:
                # 만약 20개가 넘게 있다면 error가 안남.
                score = driver.find_element(value=f'body > main > article > div.column-wrapper > div > div > section > div.search-list-restaurants-inner-wrap > ul > li:nth-child({i}) > div:nth-child({j}) > figure > figcaption > div',  by = 'css selector').text
                if score:
                    #print(score)
                    # 주소 가져오기
                    driver.find_element(value=f'body > main > article > div.column-wrapper > div > div > section > div.search-list-restaurants-inner-wrap > ul > li:nth-child({i}) > div:nth-child({j}) > figure > figcaption > div > a',  by = 'css selector').click()
                    driver.implicitly_wait(2)
                    address = driver.find_element(value=f"body > main > article > div.column-wrapper > div.column-contents > div > section.restaurant-detail > table > tbody > tr:nth-child(1) > td",  by = 'css selector').text
                    driver.back()
                    driver.implicitly_wait(2)
                    score = score+'\n'+address
                    value['mango_score'].append(score)
                else:
                    try:
                        driver.find_element(value=f"body > main > article > div.column-wrapper > div > div > section > div.paging-container > p > a:nth-child({page+1})",  by = 'css selector').click()
                        driver.implicitly_wait(2)
                        page+=1
                        return page
                    # 다음 페이지가 없다면 검색 다시
                    except:
                        return page
            except:
                # 다음 페이지
                try:
                    driver.find_element(value=f"body > main > article > div.column-wrapper > div > div > section > div.paging-container > p > a:nth-child({page+1})",  by = 'css selector').click()
                    driver.implicitly_wait(2)
                    page+=1
                    return page
                # 다음 페이지가 없다면 기존 페이지 반환
                except:
                    return page
    

In [4]:
options = webdriver.chrome.options.Options()
#options.add_argument('headless') #headless모드 브라우저가 뜨지 않고 실행됩니다.
#options.add_argument('--window-size= x, y') #실행되는 브라우저 크기를 지정할 수 있습니다.
options.add_argument('--start-maximized') #브라우저가 최대화된 상태로 실행됩니다.
options.add_argument('--start-fullscreen') #브라우저가 풀스크린 모드(F11)로 실행됩니다.
options.add_argument('--blink-settings=imagesEnabled=false') #브라우저에서 이미지 로딩을 하지 않습니다.
options.add_argument('--mute-audio') #브라우저에 음소거 옵션을 적용합니다.
#options.add_argument('incognito') #시크릿 모드의 브라우저가 실행됩니다.
driver = webdriver.Chrome('./chromedriver_win32/chromedriver.exe', options=options)
driver.get(default_url)

C:\Users\User\AppData\Local\Temp/ipykernel_15776/1104595322.py:9: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome('./chromedriver_win32/chromedriver.exe', options=options)


In [5]:
# data load
data = json.load(open(args.data_dir))
unique_data = {}
for i,j in data.items():
    if i.split()[-1].endswith('점'):
        query = ' '.join(i.split()[:-1])
    else:
        query = i
    unique_data[query]=j

In [ ]:
now = time.time()
for query, value in tqdm(unique_data.items()):
    page = 1
    current_page = -1
    value['%s_score'%args.where]=[]
    # query 입력
    # 서울로 검색하기 위함임.
    driver.find_element(value="#main-search",  by = 'css selector').send_keys('서울 '+query)
    driver.find_element(value="#main-search",  by = 'css selector').send_keys(Keys.RETURN)
    driver.implicitly_wait(args.wait_second)
    while current_page!=page:
        current_page = page
        page = get_information_from_page(value, page)
    # 재검색
    driver.get(MANGO_URL)
    driver.implicitly_wait(args.wait_second)
    logger_1.info(query)
    #logger_1.info(value)
    logger_2.info(query)
    logger_2.info(value)
    continue    
print(time.time()-now)

  0%|                                                                                         | 0/6765 [00:00<?, ?it/s]2022-11-20 01:07:42,180 - log - INFO- 혼밥대왕
2022-11-20 01:07:42,181 - log - INFO- {'소재지전체주소': '서울특별시 강서구 화곡동 24-90번지 근상프리즘주상복합아파트 2층 201호', '도로명전체주소': '서울특별시 강서구 화곡로 242, 2층 201호 (화곡동, 근상프리즘주상복합아파트)', '자치구': '강서구', 'mango_score': [None]}
  0%|                                                                               | 1/6765 [00:02<4:44:09,  2.52s/it]2022-11-20 01:08:05,939 - log - INFO- 
2022-11-20 01:08:05,940 - log - INFO- {'소재지전체주소': '서울특별시 강서구 가양동 1482 가양도시개발공사아파트(가양8단지아파트) 상가동 101호', '도로명전체주소': '서울특별시 강서구 허준로 176, 상가동 101호 (가양동, 가양도시개발공사아파트(가양8단지아파트))', '자치구': '강서구', 'mango_score': ['미라이 4.8\n가로수길 - 이자카야 / 오뎅 / 꼬치\n477,609 123\n서울특별시 강남구 논현로153길 24 끌레르빌 1F\n지번 서울시 강남구 신사동 557-25 끌레르빌 1F', '스시아라타 4.8\n여의도 - 회 / 스시\n287,701 50\n서울특별시 영등포구 국제금융로8길 16 B1 B124호\n지번 서울시 영등포구 여의도동 34-8 B1 B124호', '시라카와 4.8\n신사/압구정 - 이자카야 / 오뎅 / 꼬치\n296,065 68\n서울특별시 강남구 선릉로161길 7 1F\

In [4]:
data=json.load(open('./data/seoul/강남구_add.json'))

In [7]:
data

{'커스텀커피': {'소재지전체주소': '서울특별시 강남구 개포동 1282 개포 래미안 포레스트 ',
  '도로명전체주소': '서울특별시 강남구 개포로 264, 상가1동 지하1층 102-2호 (개포동, 개포 래미안 포레스트)',
  '자치구': '강남구',
  'mango_score': ['컨택트 4.0\n마포/공덕 - 카페 / 디저트\n3,020 7\n서울특별시 마포구 양화로10길 45\n지번 서울시 마포구 서교동 395-74',
   '커스텀커피 (합정점)\n마포/공덕 - 카페 / 디저트\n1,249 1\n서울특별시 마포구 월드컵로8길 40\n지번 서울시 마포구 서교동 381-9',
   '커스텀커피 (강남구청점)\n삼성동 - 카페 / 디저트\n210 1\n서울특별시 강남구 학동로68길 7 상가 1F 107호\n지번 서울시 강남구 삼성동 16 상가 1F 107호',
   '커스텀커피 (서초우면점)\n양재동 - 카페 / 디저트\n461 1\n서울특별시 서초구 성촌1길 12\n지번 서울시 서초구 우면동 687',
   '커스텀커피 (현대백화점 디큐브시티점)\n구로구 - 카페 / 디저트\n118 1\n서울특별시 구로구 경인로 662 B2\n지번 서울시 구로구 신도림동 692 B2',
   '커스텀커피 (방배점)\n방배/반포/잠원 - 카페 / 디저트\n51 1\n서울특별시 서초구 방배로 16 1F\n지번 서울시 서초구 방배동 1015 1F',
   '커스텀커피 (개포점)\n개포/수서/일원 - 카페 / 디저트\n35 0\n서울특별시 강남구 영동대로 22 디에이치자이개포 단지내상가 808동 107호\n지번 서울시 강남구 일원동 743 디에이치자이개포 단지내상가 808동 107호',
   '커스텀커피 (DMC가재울점)\n서대문구 - 카페 / 디저트\n3 0\n서울특별시 서대문구 가재울미래로 2 상가101동 106-1호\n지번 서울시 서대문구 남가좌동 385 상가101동 106-1호']},
 '송오브송즈로스터즈': {'소재지전체주소': '서울특별시 강남구 신사동 569-

In [ ]:
MANGO_URL = 'https://www.mangoplate.com/'
KAKAO_URL = 'https://map.kakao.com/'
GOOGLE_URL = 'https://www.google.com/maps'
# OK - 기존과 바뀜 - 함수 통일화
ALPHABET = list(string.ascii_uppercase)

logger_1, logger_2 = get_logs()
parser = argparse.ArgumentParser(description='parse')
# argument는 원하는 만큼 추가한다.
parser.add_argument('--output_dir', type=str, default = './output/seoul/mango')
parser.add_argument('--data_dir', type=str, default = './data/seoul/종로구.json')
parser.add_argument('--where', type=str, choices=['mango','google','kakao'], default='mango')
parser.add_argument('--wait_second', type=int, default = 2)
args, _ = parser.parse_known_args()
if args.where == 'mango':
    default_url = MANGO_URL
    
elif args.where == 'kakao':
    default_url = KAKAO_URL
    
elif args.where == 'google':
    default_url = GOOGLE_URL

In [ ]:
# data load
data = json.load(open(args.data_dir))
unique_data = {}
for i,j in data.items():
    if i.split()[-1].endswith('점'):
        query = ' '.join(i.split()[:-1])
    else:
        query = i
    unique_data[query]=j

In [ ]:
now = time.time()
for query, value in tqdm(unique_data.items()):
    page = 1
    current_page = -1
    value['%s_score'%args.where]=[]
    # query 입력
    # 서울로 검색하기 위함임.
    driver.find_element(value="#main-search",  by = 'css selector').send_keys('서울 '+query)
    driver.find_element(value="#main-search",  by = 'css selector').send_keys(Keys.RETURN)
    driver.implicitly_wait(args.wait_second)
    while current_page!=page:
        current_page = page
        page = get_information_from_page(value, page)
    # 재검색
    driver.get(MANGO_URL)
    driver.implicitly_wait(args.wait_second)
    logger_1.info(query)
    #logger_1.info(value)
    logger_2.info(query)
    logger_2.info(value)
    continue    
print(time.time()-now)

In [ ]:
json.dump(unique_data,open('./data/seoul/종로구_add.json','w'))